In [ ]:
#Import all the required libraries and establish CUDA for training.
import torch
import torchvision
from torch.utils.data import Dataset
import torch.nn as nn
import torchvision.transforms as transforms
import torchvision.datasets as dsets
import torch.nn.functional as F
import matplotlib.pylab as plt
import numpy as np
from torchvision import models
torch.manual_seed(2)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
train_on_gpu = torch.cuda.is_available()
if not train_on_gpu:
    print('CUDA is not available')
else:
    print('CUDA is available!')

In [ ]:
#Mount the training and testing paths on Google Drive by assigning the required paths.
from google.colab import drive, files
drive.mount('/content/drive/')
trainpath = "/content/drive/MyDrive/BTS/Train-data/"
testpath = "/content/drive/MyDrive/BTS-Test/Train-data/"

In [ ]:
#Train Transform and data loader
transform1 = transforms.Compose([transforms.Resize((224,224)),transforms.CenterCrop(size=224),transforms.ToTensor(),transforms.Normalize([0.485, 0.456, 0.406],[0.229, 0.224, 0.225])])
train_dataset = dsets.ImageFolder(root=trainpath, transform=transform1)
train_loader = torch.utils.data.DataLoader(dataset=train_dataset,batch_size=1, shuffle=True)

#Test transform and dataloader
test_transform = transforms.Compose([transforms.Resize((224,224)),transforms.CenterCrop(size=224),transforms.ToTensor(),transforms.Normalize([0.485, 0.456, 0.406],[0.229, 0.224, 0.225])])
test_dataset = dsets.ImageFolder(root=testpath, transform=test_transform)
test_loader = torch.utils.data.DataLoader(dataset=test_dataset,batch_size=1, shuffle=False)

num_epochs = 40
num_classes = 3
batch_size = 32
learning_rate = 0.001
print('there are {}  images in training set.'.format(len(train_dataset)))
print('there are {}  images in test set.'.format(len(test_dataset)))
print('there are {}  images in training loader.'.format(len(train_loader)))
print('there are {}  images in testing loader.'.format(len(test_loader)))

In [ ]:
#Now using the AlexNet
torch.hub._validate_not_a_forked_repo=lambda a,b,c: True
AlexNet_model = torch.hub.load('pytorch/vision:v0.6.0', 'alexnet', pretrained=True)

#Model description
AlexNet_model.eval()

In [ ]:
#Updating the second classifier
AlexNet_model.classifier[4] = nn.Linear(4096,1024)
#Updating the third and the last classifier that is the output layer of the network.
#Make sure to have 3 output nodes if we are going to get 3 class labels through our model.
AlexNet_model.classifier[6] = nn.Linear(1024,3)

In [ ]:
AlexNet_model.eval()

In [ ]:
model = AlexNet_model.to (device)
# Loss and optimizer
criterion = nn.CrossEntropyLoss().to (device)
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
optimizer = torch.optim.SGD(model.parameters(), lr=0.0001, momentum=0.9)

In [ ]:
#Loading the saved model where the training results have been saved already.
PATH = '/content/drive/MyDrive/S_Augmented_Rotation_3degrees_Dataset.pth'
model.load_state_dict(torch.load(PATH))

<All keys matched successfully>

In [ ]:
#Testing the model to check if I have loaded the saved model correctly.
model.eval()
with torch.no_grad():
    correct = 0
    total = 0
    for images, labels in test_loader:
        images=images.to (device)
        labels=labels.to (device)
        outputs = model(images).to(device)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

    print('Test Accuracy of the model on the  test images: {} %'.format((correct / total) * 100))

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/conv.py:456: UserWarning: Plan failed with a cudnnException: CUDNN_BACKEND_EXECUTION_PLAN_DESCRIPTOR: cudnnFinalize Descriptor Failed cudnn_status: CUDNN_STATUS_NOT_SUPPORTED (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:919.)
  return F.conv2d(input, weight, bias, self.stride,


Test Accuracy of the model on the  test images: 92.38095238095238 %


In [ ]:
import torch
import numpy as np
from sklearn.metrics import classification_report, confusion_matrix
import seaborn as sns
import matplotlib.pyplot as plt

# Testing the model to check if I have loaded the saved model correctly.
model.eval()
all_labels = []
all_predictions = []

with torch.no_grad():
    correct = 0
    total = 0
    for images, labels in test_loader:
        images = images.to(device)
        labels = labels.to(device)
        outputs = model(images).to(device)
        _, predicted = torch.max(outputs.data, 1)

        total += labels.size(0)
        correct += (predicted == labels).sum().item()

        all_labels.extend(labels.cpu().numpy())
        all_predictions.extend(predicted.cpu().numpy())

    print('Test Accuracy of the model on the test images: {} %'.format((correct / total) * 100))

# Classification Report
print("Classification Report:\n")
print(classification_report(all_labels, all_predictions))

# Confusion Matrix
conf_matrix = confusion_matrix(all_labels, all_predictions)
print("Confusion Matrix:\n")
print(conf_matrix)

# Optional: Visualize the confusion matrix using seaborn
plt.figure(figsize=(10, 8))
sns.heatmap(conf_matrix, annot=True, fmt='d', cmap='Blues')
plt.xlabel('Predicted Labels')
plt.ylabel('True Labels')
plt.title('Confusion Matrix')
plt.show()


In [ ]:
#6 layer model code
import torch
import torch.nn as nn

class DeepConvNet(nn.Module):
    def __init__(self):
        super(DeepConvNet, self).__init__()
        self.layer1 = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.layer2 = nn.Sequential(
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.layer3 = nn.Sequential(
            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.layer4 = nn.Sequential(
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.layer5 = nn.Sequential(
            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.layer6 = nn.Sequential(  # New layer added
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2, stride=2))
        self.drop_out = nn.Dropout(p=0.5)
        self.fc1 = nn.Linear(1024 * 4 * 4, 1000)  # Adjusted input size
        self.fc2 = nn.Linear(1000, 500)
        self.fc3 = nn.Linear(500, 3)

    def forward(self, x):
        # Layer 1
        out = self.layer1[0](x)  # Convolution
        print("Layer 1 Conv Output Shape:", out.shape)
        out = self.layer1[1](out)  # Batch Normalization
        print("Layer 1 BatchNorm Output Shape:", out.shape)
        out = self.layer1[2](out)  # ReLU
        print("Layer 1 ReLU Output Shape:", out.shape)
        out = self.layer1[3](out)  # MaxPool
        print("Layer 1 MaxPool Output Shape:", out.shape)
       
        # Layer 2
        out = self.layer2[0](out)  # Convolution
        print("Layer 2 Conv Output Shape:", out.shape)
        out = self.layer2[1](out)  # Batch Normalization
        print("Layer 2 BatchNorm Output Shape:", out.shape)
        out = self.layer2[2](out)  # ReLU
        print("Layer 2 ReLU Output Shape:", out.shape)
        out = self.layer2[3](out)  # MaxPool
        print("Layer 2 MaxPool Output Shape:", out.shape)
       
        # Layer 3
        out = self.layer3[0](out)  # Convolution
        print("Layer 3 Conv Output Shape:", out.shape)
        out = self.layer3[1](out)  # Batch Normalization
        print("Layer 3 BatchNorm Output Shape:", out.shape)
        out = self.layer3[2](out)  # ReLU
        print("Layer 3 ReLU Output Shape:", out.shape)
        out = self.layer3[3](out)  # MaxPool
        print("Layer 3 MaxPool Output Shape:", out.shape)
       
        # Layer 4
        out = self.layer4[0](out)  # Convolution
        print("Layer 4 Conv Output Shape:", out.shape)
        out = self.layer4[1](out)  # Batch Normalization
        print("Layer 4 BatchNorm Output Shape:", out.shape)
        out = self.layer4[2](out)  # ReLU
        print("Layer 4 ReLU Output Shape:", out.shape)
        out = self.layer4[3](out)  # MaxPool
        print("Layer 4 MaxPool Output Shape:", out.shape)
       
        # Layer 5
        out = self.layer5[0](out)  # Convolution
        print("Layer 5 Conv Output Shape:", out.shape)
        out = self.layer5[1](out)  # Batch Normalization
        print("Layer 5 BatchNorm Output Shape:", out.shape)
        out = self.layer5[2](out)  # ReLU
        print("Layer 5 ReLU Output Shape:", out.shape)
        out = self.layer5[3](out)  # MaxPool
        print("Layer 5 MaxPool Output Shape:", out.shape)
       
        # Layer 6
        out = self.layer6[0](out)  # Convolution
        print("Layer 6 Conv Output Shape:", out.shape)
        out = self.layer6[1](out)  # Batch Normalization
        print("Layer 6 BatchNorm Output Shape:", out.shape)
        out = self.layer6[2](out)  # ReLU
        print("Layer 6 ReLU Output Shape:", out.shape)
        out = self.layer6[3](out)  # MaxPool
        print("Layer 6 MaxPool Output Shape:", out.shape)
       
        # Flatten and Fully Connected Layers
        out = out.view(out.size(0), -1)
        print("Flattened Output Shape:", out.shape)
        out = self.drop_out(out)
        out = self.fc1(out)
        print("FC1 Output Shape:", out.shape)
        out = self.fc2(out)
        print("FC2 Output Shape:", out.shape)
        out = self.fc3(out)
        print("FC3 Output Shape:", out.shape)
        return out

device = torch.device("cpu")  # Use CPU
model = DeepConvNet().to(device)
print(model)